<a href="https://colab.research.google.com/github/Yurovskyy/TP3/blob/main/TP3.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [23]:
import pandas as pd
import requests
from sklearn.cluster import KMeans
from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.compose import ColumnTransformer
from sklearn.cluster import KMeans
from sklearn.pipeline import Pipeline
from sklearn.decomposition import PCA
from sklearn.manifold import TSNE
from matplotlib import pyplot as plt
import plotly.express as px

In [47]:
# @title Carregando o dataset

# URL do arquivo CSV
url = 'https://github.com/Yurovskyy/TP3/raw/main/output.csv'

# Baixar o arquivo CSV da web
response = requests.get(url)

# Verificar se a solicitação foi bem-sucedida
if response.status_code == 200:
    # Ler o conteúdo do arquivo CSV usando o Pandas
    df = pd.read_csv(url)

# Se a solicitação não for bem-sucedida
else:
    print('Falha ao baixar o arquivo CSV.')


In [3]:
# @title Exploração inicial do dataset

dimensoes = df.shape
print("Número de entradas(linhas):", dimensoes[0])
print("Número de colunas(variáveis):", dimensoes[1])

# identificar o tipo de cada variável
display(df.dtypes)

# ver as 5 primeiras entradas do conjunto de treino
display(df.head())

Número de entradas(linhas): 4944
Número de colunas(variáveis): 14


Index       float64
firm          int64
BE          float64
ME          float64
ME.lag1     float64
r_i         float64
r.3.0       float64
r.12.4      float64
AC          float64
CA          float64
DR          float64
OFC         float64
ECI         float64
industry     object
dtype: object

Index  firm            BE            ME       ME.lag1       r_i  \
0  2020.75     1  1.179763e+09  1.217182e+09  1.200622e+09  0.089471   
1  2020.50     1  1.262906e+09  1.064582e+09  1.217182e+09 -0.013699   
2  2022.00     1  1.205650e+09  1.354615e+09  1.761918e+09  0.181542   
3  2021.25     1  1.190537e+09  1.312840e+09  1.064523e+09  0.267479   
4  2023.00     1  1.072554e+09  2.471660e+09  2.544702e+09  0.042154   

      r.3.0    r.12.4        AC        CA        DR       OFC       ECI  \
0 -0.013699 -0.618101  0.500000  0.694444  0.750000  0.433333  0.805556   
1  0.142185 -0.471392  0.500000  0.611111  0.750000  0.400000  0.833333   
2  0.259363  0.039740  0.527778  0.722222  0.750000  0.666667  0.833333   
3 -0.209721  0.217958  0.500000  0.694444  0.750000  0.433333  0.805556   
4  0.029124  0.337521  0.527778  0.888889  0.958333  0.766667  0.722222   

  industry  
0   Outros  
1   Outros  
2   Outros  
3   Outros  
4   Outros

In [4]:
# @title Valores faltantes
# @markdown Como eu disse, não temos valores faltantes!

# ver a porcentagem valores faltantes
display((df.isnull().sum() / df.shape[0]).sort_values(ascending=False))

Index       0.0
firm        0.0
BE          0.0
ME          0.0
ME.lag1     0.0
r_i         0.0
r.3.0       0.0
r.12.4      0.0
AC          0.0
CA          0.0
DR          0.0
OFC         0.0
ECI         0.0
industry    0.0
dtype: float64

In [5]:
# @title Descrição dos valores categóricos

display(df.describe(include=['O']))

industry
count      4944
unique       20
top      Outros
freq       1145

In [7]:
fig = px.scatter(df,
                 x='ME',
                 y='r.12.4',
                 hover_data=["industry","firm"],
                 title="Market Value por Retorno Anual")

fig.show()

In [8]:
fig = px.scatter(df,
                 x='industry',
                 y='r.12.4',
                 hover_data=["ME","firm"],
                 title="Tipo de industria por Retorno Anual")

fig.show()

In [10]:
fig = px.scatter(df,
                 x='r.12.4',
                 y='CA',
                 hover_data=["industry","firm","ME"],
                 title="CA por Retorno Anual")

fig.show()

In [11]:
fig = px.scatter(df,
                 x='r.12.4',
                 y='AC',
                 hover_data=["industry","firm","ME"],
                 title="AC por Retorno Anual")

fig.show()

In [12]:
fig = px.scatter(df,
                 x='r.12.4',
                 y='DR',
                 hover_data=["industry","firm","ME"],
                 title="DR por Retorno Anual")

fig.show()

In [13]:
fig = px.scatter(df,
                 x='r.12.4',
                 y='OFC',
                 hover_data=["industry","firm","ME"],
                 title="OFC por Retorno Anual")

fig.show()

In [14]:
fig = px.scatter(df,
                 x='r.12.4',
                 y='ECI',
                 hover_data=["industry","firm","ME"],
                 title="ECI por Retorno Anual")

fig.show()

In [20]:
fig = px.histogram(df, x='r.12.4', title='Histograma dos valores')
fig.show()

In [40]:
display(df.describe())

Index         firm            BE            ME       ME.lag1  \
count  4944.000000  4944.000000  4.944000e+03  4.944000e+03  4.944000e+03   
mean   2021.700496   418.813714  9.244580e+09  1.647379e+10  1.655128e+10   
std       1.326880   245.360361  2.990092e+10  4.501468e+10  4.522360e+10   
min    2019.000000     1.000000  5.600000e+04  1.597143e+06  1.597557e+06   
25%    2020.500000   209.000000  7.253755e+08  8.281819e+08  8.229385e+08   
50%    2021.750000   405.000000  1.794868e+09  3.431592e+09  3.423414e+09   
75%    2022.750000   622.000000  6.121884e+09  1.161053e+10  1.183215e+10   
max    2023.750000   860.000000  4.341940e+11  5.705210e+11  5.705210e+11   

               r_i        r.3.0       r.12.4           AC           CA  \
count  4944.000000  4944.000000  4944.000000  4944.000000  4944.000000   
mean      0.003556     0.003051     0.017635     0.528727     0.781031   
std       0.275630     0.276638     0.441591     0.148566     0.130017   
min      -2.266958    -1.392217    -1.960695     0.194444     0.361111   
25%      -0.121592    -0.126219    -0.211830     0.416667     0.694444   
50%       0.012751     0.009830     0.021291     0.527778     0.805556   
75%       0.148643     0.151809     0.254705     0.638889     0.888889   
max       1.516664     1.516664     5.134580     0.833333     1.000000   

                DR          OFC          ECI  
count  4944.000000  4944.000000  4944.000000  
mean      0.845292     0.710720     0.764979  
std       0.135652     0.165161     0.139815  
min       0.333333     0.233333     0.305556  
25%       0.791667     0.600000     0.694444  
50%       0.875000     0.733333     0.777778  
75%       0.958333     0.833333     0.861111  
max       1.000000     1.000000     1.000000

In [48]:
df = df.drop(columns=["industry"])

In [49]:
scaler = StandardScaler()
values = scaler.fit_transform(df[["AC","CA","DR","OFC","ECI"]])

kmeans = KMeans(n_clusters=7, random_state=42)
df['Cluster'] = kmeans.fit_predict(values)

fig = px.scatter(df, x='Index', y='r.12.4', color='Cluster', hover_data=["Index","firm","BE","ME","r.12.4","AC","CA","DR","OFC","ECI"], title='Clusterização')
fig.show()

/usr/local/lib/python3.10/dist-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning:

The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning



In [50]:

pca = PCA(n_components=2)
X_reduced = pca.fit_transform(df)

fig = px.scatter(X_reduced, x=0, y=1, color=df["Cluster"].astype(str), title="Clusterização com KMeans")
fig.show()

In [51]:
# Converter X_reduced para DataFrame e adicionar colunas originais
df_reduced = pd.DataFrame(X_reduced, columns=['PC1', 'PC2'])
df_reduced["Cluster"] = df["Cluster"].astype(str)
df_reduced["Index"] = df.index
df_reduced["firm"] = df["firm"]
df_reduced["BE"] = df["BE"]
df_reduced["ME"] = df["ME"]
df_reduced["r.12.4"] = df["r.12.4"]
df_reduced["AC"] = df["AC"]
df_reduced["CA"] = df["CA"]
df_reduced["DR"] = df["DR"]
df_reduced["OFC"] = df["OFC"]
df_reduced["ECI"] = df["ECI"]

# Gerar o gráfico com hover_data
fig = px.scatter(
    df_reduced, x='PC1', y='PC2', color="Cluster",
    hover_data=["Index", "firm", "BE", "ME", "r.12.4", "AC", "CA", "DR", "OFC", "ECI"],
    title="Clusterização com KMeans"
)
fig.show()

In [52]:
for cluster in df_reduced["Cluster"].unique():
    print(f"Resumo estatístico do Cluster {cluster}:")
    display(df_reduced[df_reduced["Cluster"] == cluster].describe())
    print("\n" + "="*50 + "\n")

Resumo estatístico do Cluster 6:


PC1           PC2        Index        firm            BE  \
count  4.140000e+02  4.140000e+02   414.000000  414.000000  4.140000e+02   
mean  -2.045668e+10  6.987644e+08  2321.838164  393.705314  1.717711e+09   
std    8.032164e+09  1.592222e+09  1425.900518  245.753001  2.672070e+09   
min   -2.508968e+10 -1.268995e+10     0.000000    1.000000  4.371000e+06   
25%   -2.447795e+10  5.728908e+08  1188.250000  199.000000  2.593632e+08   
50%   -2.331022e+10  8.470726e+08  2144.500000  350.000000  7.153825e+08   
75%   -2.080896e+10  1.085259e+09  3479.500000  581.000000  1.629835e+09   
max    3.722721e+10  6.854908e+09  4815.000000  845.000000  1.549096e+10   

                 ME      r.12.4          AC          CA          DR  \
count  4.140000e+02  414.000000  414.000000  414.000000  414.000000   
mean   3.059136e+09    0.052593    0.560722    0.665258    0.695652   
std    5.632275e+09    0.533772    0.079849    0.062457    0.104818   
min    4.231305e+06   -1.354667    0.416667    0.527778    0.458333   
25%    3.184882e+08   -0.238872    0.500000    0.611111    0.625000   
50%    1.136524e+09    0.024897    0.555556    0.666667    0.708333   
75%    3.042446e+09    0.263976    0.611111    0.722222    0.791667   
max    5.121581e+10    5.134580    0.777778    0.777778    1.000000   

              OFC         ECI  
count  414.000000  414.000000  
mean     0.485990    0.640835  
std      0.100775    0.111388  
min      0.233333    0.333333  
25%      0.400000    0.555556  
50%      0.500000    0.638889  
75%      0.566667    0.694444  
max      0.766667    0.944444



Resumo estatístico do Cluster 4:


PC1           PC2        Index        firm            BE  \
count  6.850000e+02  6.850000e+02   685.000000  685.000000  6.850000e+02   
mean  -1.180955e+10 -9.242399e+06  2252.846715  381.156204  4.520510e+09   
std    2.302131e+10  4.867377e+09  1398.619604  239.411127  8.168949e+09   
min   -2.508095e+10 -2.442977e+10     2.000000    1.000000  3.612000e+06   
25%   -2.366225e+10 -3.490660e+08  1022.000000  174.000000  8.488310e+08   
50%   -2.000240e+10  8.494249e+08  2213.000000  360.000000  1.671413e+09   
75%   -9.225039e+09  1.440109e+09  3303.000000  541.000000  5.221418e+09   
max    1.445133e+11  1.783044e+10  4850.000000  849.000000  5.869600e+10   

                 ME      r.12.4          AC          CA          DR  \
count  6.850000e+02  685.000000  685.000000  685.000000  685.000000   
mean   8.778524e+09    0.060095    0.403771    0.703366    0.774574   
std    1.565734e+10    0.404275    0.079100    0.071212    0.077555   
min    1.147860e+07   -1.217108    0.194444    0.500000    0.541667   
25%    7.748884e+08   -0.155352    0.361111    0.666667    0.750000   
50%    3.189989e+09    0.042147    0.388889    0.722222    0.791667   
75%    9.936395e+09    0.267751    0.472222    0.750000    0.833333   
max    1.183928e+11    1.519084    0.583333    0.888889    0.916667   

              OFC         ECI  
count  685.000000  685.000000  
mean     0.741119    0.751825  
std      0.089004    0.087365  
min      0.533333    0.527778  
25%      0.666667    0.694444  
50%      0.733333    0.750000  
75%      0.800000    0.833333  
max      0.966667    0.944444



Resumo estatístico do Cluster 5:


...

PC1           PC2        Index        firm            BE  \
count  9.300000e+02  9.300000e+02   930.000000  930.000000  9.300000e+02   
mean   2.823676e+10  9.029656e+08  2895.492473  492.966667  2.134618e+10   
std    1.174489e+11  2.357159e+10  1454.415205  252.612788  5.689479e+10   
min   -2.501985e+10 -1.116768e+11    63.000000   11.000000  2.250000e+06   
25%   -2.054713e+10 -2.496566e+09  1726.250000  301.000000  1.757499e+09   
50%   -1.130822e+10  9.092064e+08  3191.500000  529.000000  4.841190e+09   
75%    1.537235e+10  2.754151e+09  4151.000000  711.000000  1.147529e+10   
max    7.535930e+11  1.634050e+11  4926.000000  859.000000  4.341940e+11   

                 ME      r.12.4          AC          CA          DR  \
count  9.300000e+02  930.000000  930.000000  930.000000  930.000000   
mean   3.445251e+10   -0.029575    0.697073    0.925388    0.962993   
std    7.457216e+10    0.434511    0.074127    0.055886    0.051593   
min    5.600000e+07   -1.960695    0.527778    0.777778    0.708333   
25%    2.751450e+09   -0.256026    0.638889    0.888889    0.916667   
50%    8.745123e+09   -0.002839    0.694444    0.944444    1.000000   
75%    2.842779e+10    0.215220    0.750000    0.972222    1.000000   
max    5.705210e+11    1.872125    0.833333    1.000000    1.000000   

              OFC         ECI  
count  930.000000  930.000000  
mean     0.874839    0.884857  
std      0.076805    0.065016  
min      0.633333    0.638889  
25%      0.833333    0.833333  
50%      0.866667    0.888889  
75%      0.925000    0.916667  
max      1.000000    1.000000



Resumo estatístico do Cluster 3:


PC1           PC2        Index        firm            BE  \
count  6.520000e+02  6.520000e+02   652.000000  652.000000  6.520000e+02   
mean  -1.497992e+10 -3.546841e+08  2390.662577  403.976994  2.938578e+09   
std    1.481910e+10  3.213322e+09  1402.825767  240.551449  4.072600e+09   
min   -2.509885e+10 -2.166053e+10    72.000000   15.000000  3.790000e+05   
25%   -2.368068e+10 -7.795561e+08  1346.750000  235.000000  5.683340e+08   
50%   -2.057383e+10  7.473566e+08  2378.500000  395.000000  1.479118e+09   
75%   -1.355048e+10  1.131432e+09  3626.500000  597.000000  3.410286e+09   
max    7.736689e+10  9.065685e+09  4942.000000  860.000000  2.719363e+10   

                 ME      r.12.4          AC          CA          DR  \
count  6.520000e+02  652.000000  652.000000  652.000000  652.000000   
mean   6.904001e+09   -0.013069    0.479337    0.772708    0.906378   
std    1.037387e+10    0.431321    0.081734    0.074536    0.054585   
min    1.597143e+06   -1.817558    0.250000    0.583333    0.791667   
25%    8.069475e+08   -0.232188    0.416667    0.722222    0.875000   
50%    2.895926e+09   -0.004709    0.472222    0.777778    0.916667   
75%    8.001438e+09    0.213268    0.527778    0.805556    0.916667   
max    7.350282e+10    1.511864    0.722222    1.000000    1.000000   

              OFC         ECI  
count  652.000000  652.000000  
mean     0.583180    0.719751  
std      0.084838    0.096758  
min      0.366667    0.500000  
25%      0.533333    0.638889  
50%      0.600000    0.722222  
75%      0.633333    0.777778  
max      0.800000    0.916667



Resumo estatístico do Cluster 0:


PC1           PC2        Index        firm            BE  \
count  4.930000e+02  4.930000e+02   493.000000  493.000000  4.930000e+02   
mean  -2.313797e+10  7.439836e+08  2526.841785  429.537525  6.884072e+08   
std    3.361837e+09  8.980749e+08  1463.819702  250.748346  9.601090e+08   
min   -2.507891e+10 -3.799945e+09   325.000000   63.000000  2.320000e+05   
25%   -2.480213e+10  7.516082e+08  1371.000000  242.000000  1.206950e+08   
50%   -2.442272e+10  8.694721e+08  2465.000000  402.000000  3.532133e+08   
75%   -2.360597e+10  1.018670e+09  3774.000000  635.000000  9.589190e+08   
max   -7.409746e+09  2.890569e+09  4906.000000  855.000000  6.261196e+09   

                 ME      r.12.4          AC          CA          DR  \
count  4.930000e+02  493.000000  493.000000  493.000000  493.000000   
mean   1.283985e+09    0.134468    0.331925    0.548400    0.603110   
std    2.384021e+09    0.428780    0.075698    0.059089    0.107697   
min    1.116357e+07   -1.145132    0.222222    0.361111    0.333333   
25%    1.783246e+08   -0.091184    0.277778    0.527778    0.541667   
50%    4.333897e+08    0.099216    0.333333    0.555556    0.583333   
75%    9.084950e+08    0.364420    0.361111    0.583333    0.666667   
max    1.511550e+10    2.926328    0.555556    0.722222    0.875000   

              OFC         ECI  
count  493.000000  493.000000  
mean     0.486004    0.511494  
std      0.117391    0.114446  
min      0.266667    0.305556  
25%      0.400000    0.416667  
50%      0.466667    0.527778  
75%      0.566667    0.583333  
max      0.733333    0.833333